## **Initialization**

In [1]:
# Install necessary packages if they are not already installed

!pip install gurobipy   # Gurobi optimization solver
!pip install pandas     # Pandas for data analysis and manipulation
!pip install folium     # Folium for creating interactive maps
!pip install geopy      # Geopy for computing distances and working with geographic data
!pip install gdown

!pip install scgraph==2.1.0         # Python package used to compute paths and distances on a real-world transportation network
!pip install scgraph_data==2.0.0    # Python package used to compute paths and distances on a real-world transportation network
!pip install xlsxwriter

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.5/14.5 MB 18.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 944.1/944.1 kB 52.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 169.4/169.4 kB 12.3 MB/s eta 0:00:00


In [2]:
# Import all required packages

import pandas as pd                   # For data manipulation and analysis
import gurobipy as grb                # Gurobi optimization library for solving mathematical models
import folium                         # For creating interactive maps
import folium.plugins as plugins      # Additional plugins for folium
from geopy.distance import geodesic   # For calculating geodesic distances between two points
import gdown

import scgraph                                                  # For computing paths and distances on a real-world transportation network
from scgraph.geographs.us_freeway import us_freeway_geograph    # Data on US highway network (for road paths and distances)
from scgraph.geographs.marnet import marnet_geograph            # Data on maritime routes (for ocean paths and distances)
import os
from google.colab import drive
import numpy as np

import gurobipy as gp
from gurobipy import GRB

## **Helper functions**

### **Plotting nodes on a map**

In [3]:
def plot_nodes(map, nodes, icon, active_color, background_color, inactive_color='grey'):
    for node in nodes.values():
        is_warehouse = (icon == 'warehouse')
        is_active = node.active

        # Style adjustments for warehouse visibility
        icon_size = [34, 34] if is_warehouse else [20, 20]
        font_size = '20px' if is_warehouse else '12px'
        border_width = 2 if is_warehouse else 1
        z_index = 1000 if is_warehouse else 500

        # Style the icon's contents
        inner_icon_style = (
            f"font-size:{font_size};"
            "display:flex;"
            "align-items:center;"
            "justify-content:center;"
            "text-align:center;"
        )

        marker = folium.Marker(
            location=[node.lat, node.lon],
            popup=f"{node.ID} - {node.name}",
            icon=plugins.BeautifyIcon(
                icon=icon,
                icon_shape="circle",
                icon_size=icon_size,
                border_width=border_width,
                text_color=active_color if is_active else inactive_color,
                border_color=active_color if is_active else inactive_color,
                background_color='white' if is_warehouse else background_color,
                inner_icon_style=inner_icon_style
            ),
            z_index_offset=z_index
        )

        marker.add_to(map)


### **Computing the shortest path between two points on a real road or ocean network**

In [4]:
# Function for computing the shortest path between two points on a real road or ocean network

def shortest_path(origin, destination, mode, result, unit='mi'):

    # Extract coordinates from origin and destination objects
    origin_coordinates = (origin.lat, origin.lon)
    destination_coordinates = (destination.lat, destination.lon)

    # Calculate the shortest path on the ocean network
    if mode == 'ocean':
        output = marnet_geograph.get_shortest_path(
            origin_node={"latitude": origin.lat, "longitude": origin.lon},
            destination_node={"latitude": destination.lat, "longitude": destination.lon},
            output_units= unit
        )

    # Calculate the shortest path on the road network
    elif mode == 'road':
        output = us_freeway_geograph.get_shortest_path(
            origin_node={"latitude": origin.lat, "longitude": origin.lon},
            destination_node={"latitude": destination.lat, "longitude": destination.lon},
            output_units= unit
        )

    # Return the total distance of the path
    if result == 'distance':
        return output['length']

    # Return the coordinates representing the path
    elif result == 'coordinate_path':
        return output['coordinate_path']


### **Plotting flows on a map**

In [5]:
# Defining a function to plot flows on a map using folium

def plot_flows(map,                   # Folium map object where flows will be plotted.
               vars,                  # Dictionary of decision variables from the optimization model
               nodes,                 # Dictionary of node objects
               max_width = 30,        # Maximum line width for the flows, default is 30
               color = 'grey',        # Color of the lines representing flows, default is grey
               opacity = 0.5):        # Opacity of the lines, default is 0.5

    # Find the maximum flow value to normalize line widths
    max_val = max([var.X for (node1_key, node2_key), var in vars.items()])

    # Iterate over flow decision variables (keys represent node pairs)
    for (node1_key, node2_key), var in vars.items():

        # Plot only positive flows
        if var.X > 0:

            # Get the coordinates of the nodes for plotting the line
            points = [[nodes[node1_key].lat, nodes[node1_key].lon],
                      [nodes[node2_key].lat, nodes[node2_key].lon]]


            # Add a PolyLine to the map to represent the flow between the nodes
            folium.PolyLine(points,
                            color=color,                                # Set the color of the line
                            weight=var.X / max_val * max_width,         # Normalize line width based on flow value
                            opacity=opacity,                            # Set line opacity
                            popup=var.X).add_to(map)                    # Show the flow value in a popup on the map


### **Plotting flows (real network) on the map**

In [6]:
# Functions that adjust the arc path to ensure longitude continuity across the globe

def adjustArcPath(path):
    for index in range(1, len(path)):
        x = path[index][1]
        prevX = path[index - 1][1]
        path[index][1] = x - (round((x - prevX)/360,0) * 360)
    return path

def modifyArcPathLong(points, amount):
    return [[i[0], i[1]+amount] for i in points]

def getCleanArcPath(path):
    path = adjustArcPath(path)
    return [
        path,
        modifyArcPathLong(path, 360),
        modifyArcPathLong(path, -360),
        modifyArcPathLong(path, 720),
        modifyArcPathLong(path, -720)
    ]

# Plots real flows on a Folium map based on optimization model results

def plot_real_flows(map,              # Folium map object where flows will be plotted.
               vars,                  # Dictionary of flow decision variables from the optimization model
               nodes,                 # Dictionary of node objects
               mode,                  # Transportation mode (road or ocean)
               max_width = 30,        # Maximum line width for the flows, default is 30
               color = 'grey',        # Color of the lines representing flows, default is grey
               opacity = 0.5):        # Opacity of the lines, default is 0.5

    # Find the maximum flow value to normalize line widths
    max_val = max([var.X for (node1_key, node2_key), var in vars.items()])

    # Iterate over flow decision variables (keys represent node pairs)
    for (node1_key, node2_key), var in vars.items():

        # Plot only positive flows
        if var.X > 0:

            # Get the shortest path coordinates for the node pair
            path = shortest_path(nodes[node1_key], nodes[node2_key], mode = mode, result = 'coordinate_path')

            # Add the path as a polyline on the map, with width proportional to the flow value
            folium.PolyLine(getCleanArcPath(path),
                      color=color,
                      weight=var.X / max_val * max_width,   # Normalize weight by maximum flow value
                      opacity=opacity).add_to(map)


## **Data setup and preprocessing**

#### Reading input files

In [7]:
# Mount Google Drive
drive.mount('/content/drive')

# Set the path to your folder in Google Drive
folder_path = "/content/drive/My Drive/SCM.800/Models/Model_1/"  # Change to your actual folder name

# Read Customer file
customers_file = os.path.join(folder_path, "m_customers.csv")
customers_df = pd.read_csv(customers_file)
customers_df['customer_id'] = customers_df['customer_id'].astype(str)

# Read Materials file
materials_file = os.path.join(folder_path, "m_materials.csv")
materials_df = pd.read_csv(materials_file)
materials_df['material_id'] = materials_df['material_id'].astype(str)

# Read Warehouse file
warehouses_file = os.path.join(folder_path, "m_warehouses.csv")
warehouses_df = pd.read_csv(warehouses_file)

# Read Demand file
demand_file = os.path.join(folder_path, "m_demand.csv")
demand_df = pd.read_csv(demand_file)
demand_df['customer_id'] = demand_df['customer_id'].astype(str)

Mounted at /content/drive


In [8]:
# Validation
print(customers_df.info())
print(materials_df.info())
print(warehouses_df.info())
print(demand_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2300 entries, 0 to 2299
Data columns (total 11 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   customer_id    2300 non-null   object 
 1   customer_name  2300 non-null   object 
 2   address        2299 non-null   object 
 3   city           2300 non-null   object 
 4   state          2300 non-null   object 
 5   country        2300 non-null   object 
 6   zipcode        2300 non-null   int64  
 7   lat            2300 non-null   float64
 8   lon            2300 non-null   float64
 9   t_mode         226 non-null    object 
 10  h_served_from  2300 non-null   object 
dtypes: float64(2), int64(1), object(8)
memory usage: 197.8+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 103 entries, 0 to 102
Data columns (total 12 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   material_id    103 non-null    object 
 1   material_n

#### Data cleaning

In [9]:
# Only consider customers in continental US
min_lat, max_lat = 24.396308, 49.384358
min_lon, max_lon = -125.0, -66.93457

customers_df = customers_df[
    (customers_df['lat'] >= min_lat) &
    (customers_df['lat'] <= max_lat) &
    (customers_df['lon'] >= min_lon) &
    (customers_df['lon'] <= max_lon)]

customers_df

customer_id                      customer_name  \
6           1506                    Bergen Brunswig   
7           1509                    Bergen Brunswig   
8           1510                             Bergen   
9           1783                Oncology Supply Co.   
10          1969              Critical Care Systems   
...          ...                                ...   
2295    90542725             Wyoming State Hospital   
2296    90542726     State Of Wyoming Department Of   
2297    90542727          Veteran'S Home Of Wyoming   
2298    90590482  Coram Alternate Site Services Inc   
2299    90603231                       90 Mdss/Sgsm   

                        address           city state country  zipcode  \
6         85 Sidney Phillips Dr         Mobile    AL      US    36607   
7           2061 W Fairview Ave     Montgomery    AL      US    36108   
8     172 Cahaba Valley Parkway         Pelham    AL      US    35124   
9     2811 Horace Shepard Drive         Dothan    AL      US    36303   
10         107A David Green Rd.     Birmingham    AL      US    35244   
...                         ...            ...   ...     ...      ...   
2295      831 Highway 150 South       Evanston    WY      US    82931   
2296       1520 East 5Th Street       Cheyenne    WY      US    82002   
2297         700 Veterans' Lane        Buffalo    WY      US    82834   
2298         136 South Mckinley         Casper    WY      US    82601   
2299  6900 Alden Drive Bldg 160  Fe Warren Afb    WY      US    82005   

            lat         lon t_mode h_served_from  
6     30.698586  -88.105780    NaN           KDC  
7     32.340688  -86.373820    NaN           KDC  
8     33.293157  -86.767961    NaN           KDC  
9     31.266568  -85.401317    NaN           KDC  
10    33.352918  -86.825333    NaN           KDC  
...         ...         ...    ...           ...  
2295  41.261943 -110.919995    NaN           HDC  
2296  41.327351 -104.666365    NaN           HDC  
2297  44.122611 -106.561068    NaN           HDC  
2298  42.859875 -106.312561    NaN           HDC  
2299  41.140250 -104.874531    NaN           HDC  

[2294 rows x 11 columns]

In [10]:
# Ensure consistent types
customers_df['customer_id'] = customers_df['customer_id'].astype(int)
materials_df['material_id'] = materials_df['material_id'].astype(int)
demand_df['customer_id'] = demand_df['customer_id'].astype(int)
demand_df['material_id'] = demand_df['material_id'].astype(int)

# Create all combinations of customer_id and material_id
full_index = pd.MultiIndex.from_product(
    [customers_df['customer_id'].unique(), materials_df['material_id'].unique()],
    names=['customer_id', 'material_id']
)

# Build full demand DataFrame
full_demand_df = pd.DataFrame(index=full_index).reset_index()

# Merge and fill missing demands
full_demand_df = full_demand_df.merge(demand_df, on=['customer_id', 'material_id'], how='left')
full_demand_df['demand'] = full_demand_df['demand'].fillna(0.5)

# Overwrite demand_df
demand_df = full_demand_df

# Check total demand and specific pair
total_demand = demand_df['demand'].sum()
print(f"Total demand: {total_demand}")

Total demand: 2218865.5


In [11]:
customers_df['t_mode'].value_counts(dropna=False)

t_mode
NaN                          2068
UPS Next Day Air              124
Fedex Next Day                 68
Same Day Truck                 18
1 Day Truck                    10
UPS 2 Day Air                   3
2 Day Truck                     1
FedEx Freight 1 day - LTL       1
Fedex Second Day                1
Name: count, dtype: int64

In [12]:
# # Function to classify transportation mode
customers_df['t_mode'] = customers_df['t_mode'].apply(
    lambda x: 'AIR' if x in ['UPS Next Day Air', 'UPS 2 Day Air'] else 'ROAD'
)
customers_df['t_mode'].value_counts(dropna=False)

t_mode
ROAD    2167
AIR      127
Name: count, dtype: int64

In [13]:
# Create Warehouse by Temperature zone
warehouses_df['warehouse_id']= warehouses_df['warehouse_id']+'_'+warehouses_df['t_zone']
warehouses_df['warehouse_name']= warehouses_df['warehouse_name']+'_'+warehouses_df['t_zone']
warehouses_df

warehouse_id warehouse_name t_zone        lat         lon  capacity
0        KDC_R     Kentucky_R      R  38.163648  -85.887391      1479
1        HDC_R    Hillsboro_R      R  45.555623 -122.926376       732
2        UPS_R          UPS_R      R  38.124110  -85.780763      1005
3        KDC_A     Kentucky_A      A  38.163648  -85.887391      5516
4        HDC_A    Hillsboro_A      A  45.555623 -122.926376       124
5        UPS_A          UPS_A      A  38.124110  -85.780763      1005

In [14]:
materials_df['cost'] = pd.to_numeric(materials_df['cost'], errors='coerce')
materials_df

material_id                      material_name    product t_zone  \
0       10202843    ACTEMRA 162MG/0.9ML 1ASDA SC US    ACTEMRA      R   
1       10216200    ACTEMRA 162MG/0.9ML 1ASDA SC US    ACTEMRA      R   
2       10242244    ACTEMRA 162MG/0.9ML 1ASDA SC US    ACTEMRA      R   
3       10252926  ACTEMRA 162MG/0.9ML 1ASDA SC US-S    ACTEMRA      R   
4       10213717    ACTEMRA 162MG/0.9ML 1ASSD SC US    ACTEMRA      R   
..           ...                                ...        ...    ...   
98      10196713         XOLAIR VILY 150MG/0ML 1 US     XOLAIR      R   
99      10206065          ZELBORAF 240MG 112TAFI US   ZELBORAF      A   
100     10233000          ZELBORAF 240MG 112TAFI US   ZELBORAF      A   
101     11004892      ZUNOVO 920MG/23ML 1VIAL SC US  TRADENAME      R   
102     11020776    ZUNOVO 920MG/23ML 1VIAL SC US-S  TRADENAME      R   

     med_class  rev_class  units_pallet  weight       cost  map_KDC  map_HDC  \
0            3          1          1440   0.240    9390.11        1        1   
1            3          1          1440   0.240    9390.11        1        1   
2            3          1          1440   0.240    9390.11        1        1   
3            3          1          1440   0.160    1574.95        1        1   
4            3          1          1440   0.160    9390.11        1        1   
..         ...        ...           ...     ...        ...      ...      ...   
98           1          1          6000   0.100     444.38        1        1   
99           3          4           960   0.470    4342.36        1        1   
100          3          4           960   0.470    3539.82        1        1   
101          3          4          2688   0.193  384399.66        1        1   
102          3          4          2688   0.193  402459.23        1        1   

     map_UPS  
0          1  
1          1  
2          1  
3          0  
4          1  
..       ...  
98         1  
99         1  
100        1  
101        1  
102        1  

[103 rows x 12 columns]

#### Definition of Classes

In [15]:
# Class representing a Customer object
class Customer():
    def __init__(self, ID, name, state, lat, lon, t_mode, h_served_from):
        self.ID = ID                   # Customer's ID
        self.name = name                # Customer's name
        self.state = state                       # Customer's state
        self.lat = lat                           # Customer's latitude
        self.lon = lon                           # Customer's longitude
        self.t_mode = t_mode         # Customer's transportation mode
        self.h_served_from = h_served_from
        self.active = True                       # Initializing node as active

In [16]:
# Class representing a Warehouse object

class Warehouse():
    def __init__(self, ID, name, t_zone, lat, lon, capacity):
        self.ID = ID                 # Warehouse's ID
        self.name = name              # Warehouse's name
        self.t_zone = t_zone                    # Warehouse's temperature zone
        self.lat = lat                          # Warehouse's latitude
        self.lon = lon                          # Warehouse's longitude
        self.capacity = capacity                # Warehouse's capacity
        self.active = True                      # Initializing node as active

In [17]:
# Class representing a Material object

class Material():
    def __init__(self, ID, name, product, t_zone, med_class, rev_class, units_pallet, weight, cost):
        self.ID = ID                            # Material's ID
        self.name = name                        # Material's name
        self.product = product                  # Material's product
        self.t_zone = t_zone                    # Material's temperature zone
        self.med_class = med_class              # Material's medical class
        self.rev_class = rev_class              # Material's revenue class
        self.units_pallet = units_pallet        # Material's units per pallet
        self.weight = weight                    # Material's weight
        self.cost = cost                        # Material's cost

        self.active = True                      # Initializing node as active

#### Creating node objects

In [18]:
nodes = dict()

In [19]:
# Creating a dictionary of customer objects
customers = dict()
for i, row in customers_df.iterrows():
    customers[row['customer_id']] = Customer(   # Use the correct column name
        ID=row['customer_id'],                  # Customer's ID
        name=row['customer_name'],              # Customer's name
        state=row['state'],                     # Customer's state
        lat=row['lat'],                         # Customer's latitude
        lon=row['lon'],                         # Customer's longitude
        t_mode=row['t_mode'],        # Customer's transportation mode
        h_served_from=row['h_served_from'],
)
# Merging the customers dictionary into the existing nodes dictionary
nodes = {**nodes, **customers}


In [20]:
# Creating a dictionary of warehouse objects
warehouses = dict()
for i, row in warehouses_df.iterrows():
    warehouses[row['warehouse_id']] = Warehouse(
        ID=row['warehouse_id'],                 # Warehouse's ID
        name=row['warehouse_name'],             # Warehouse's name
        t_zone=row['t_zone'],                   # Warehouse's temperature zone
        lat=row['lat'],                         # Warehouse's latitude
        lon=row['lon'],                         # Warehouse's longitude
        capacity=row['capacity']                # Warehouse's capacity
    )

# Merging the warehouse dictionary into the existing nodes dictionary
nodes = {**nodes, **warehouses}

In [21]:
# Creating a dictionary of materials objects
materials = dict()
for i, row in materials_df.iterrows():
    materials[row['material_id']] = Material(
        ID=row['material_id'],            # Material's ID
        name=row['material_name'],        # Material's name
        product=row['product'],           # Material's product category
        t_zone=row['t_zone'],             # Temperature zone (R or A)
        med_class=row['med_class'],       # Medical classification
        rev_class=row['rev_class'],       # Revenue classification
        units_pallet=row['units_pallet'], # Units per pallet
        weight=row['weight'],             # Weight per unit
        cost=row['cost']                  # Cost per unit
    )

In [22]:
len(nodes)

2300

#### Visualizing node objects

In [23]:
# Create a new map centered on US with a zoom level of 5
map = folium.Map([40, -100.0], zoom_start=5)

# Plot customer locations with a store icon, green color, and yellow background
plot_nodes(map=map, nodes=customers, icon='store', active_color='gray', background_color='white')

# Plot warehouse locations with a warehouse icon, blue color, and yellow background
plot_nodes(map=map, nodes=warehouses, icon='warehouse', active_color='blue', background_color='light blue')

# Add a tile layer for better map visualization (cartodbpositron theme)
folium.TileLayer('cartodbpositron').add_to(map)

# Display the map with all the plotted data
map

#### Arc distances

In [24]:
# Creating a dictionary containing distances between warehouses and customers

distances = dict()
for w, warehouse in warehouses.items():
  for c, customer in customers.items():
      distances[w, c] = shortest_path(origin = warehouse, destination = customer, mode = 'road', result = 'distance', unit = 'mi')

len(distances)

13764

#### Arc costs

## **Optimization model**

### **Creating and solving the optimization model**

In [63]:
#Gurobi License
options = {
    "WLSACCESSID": "8e653134-246b-4dfe-acd2-f7cc257a56c9",
    "WLSSECRET": "b39fcb22-3cfa-4ad5-a602-d236418be3e6",
    "LICENSEID": 2575051,
}

# Initializing the model
e = grb.Env("gurobi.log", params=options)
#e.setParam('OutputFlag', 0)
model = grb.Model("Model 1", env=e)

Set parameter WLSAccessID
Set parameter WLSSecret
Set parameter LicenseID to value 2575051
Set parameter LogFile to value "gurobi.log"
Academic license 2575051 - for non-commercial use only - registered to di___@mit.edu


In [64]:
# Sets
W = list(warehouses.keys())  # Warehouses
C = list(customers.keys())   # Customers
K = list(materials.keys())   # SKUs


# Parameters
s = {w: warehouses[w].capacity for w in W}  # Warehouse capacities
u = {k: materials[k].units_pallet for k in K}  # Units per pallet per SKU
gamma = demand_df.set_index(['customer_id', 'material_id'])['demand'].to_dict()



# Coefficients for cost and emissions
cost_intercept = {'ROAD': 111.0641, 'AIR': 755.5454}
cost_per_mile = {'ROAD': 0.0488, 'AIR': 0.2035}
cost_per_lb = {'ROAD': 0.1, 'AIR': 0.0024}

emissions_intercept = {'ROAD': 0, 'AIR': 0}
emissions_per_mile = {'ROAD': 0.1353, 'AIR': 0.8784}
emissions_per_lb = {'ROAD': 0.0195, 'AIR': 4.0776}


# Map of customer_id -> t_mode
t_mode = {row['customer_id']: row['t_mode'] for _, row in customers_df.iterrows()}

# Penalty for mismatched temperature zones
M = 1e10

# Compute cost and emission per unit
tc = {
    (i, j, k): (
        # cost_intercept[t_mode[j]] +                                       #Only using Variable cost
        # materials[k].weight * cost_per_lb[t_mode[j]] +
        distances[i, j] * cost_per_mile[t_mode[j]]
    ) * (1 if warehouses[i].t_zone == materials[k].t_zone else M)
    for i in W for j in C for k in K
}

em = {
    (i, j, k): (
        # emissions_intercept[t_mode[j]] +                                  #Only using Variable cost
        # materials[k].weight * emissions_per_lb[t_mode[j]] +
        distances[i, j] * emissions_per_mile[t_mode[j]]
    ) * (1 if warehouses[i].t_zone == materials[k].t_zone else M)
    for i in W for j in C for k in K
}


# Weights for minimization priority
w_e = 0.75   #emissions
w_c = 0.25   #transportation_cost

In [65]:
# Decision variables
x = model.addVars(W, C, K, vtype=GRB.CONTINUOUS, name="flow")
pallets_used = model.addVars(W, K, vtype=GRB.INTEGER, name="pallets_used")

t_cost = sum(
    tc[i, j, k] * x[i, j, k]
    for i in W for j in C for k in K
)

emissions = sum(
    em[i, j, k] * x[i, j, k]
    for i in W for j in C for k in K
)

# Set the objective to minimize the weighted sum of cost and emissions
model.setObjective(w_c * t_cost + w_e * emissions, GRB.MINIMIZE)




# Constraints

# Demand satisfaction constraint
for j in C:
    for k in K:
        model.addConstr(
            sum(x[i, j, k] for i in W) >= gamma[j, k],
            name=f"demand_{j}_{k}")

# Warehouse capacity constraint
for i in W:
        for k in K:
            model.addConstr(
                pallets_used[i, k] >= gp.quicksum(x[i, j, k] / u[k] for j in C),
                name=f"pallet_calc_{i}_{k}"
            )

        # Ensure total pallets used do not exceed warehouse capacity
        model.addConstr(
            gp.quicksum(pallets_used[i, k] for k in K) <= s[i],
            name=f"capacity_{i}"
        )

# Big Customers only from KDC constraint
RC = [90631576, 90584135, 90589939, 16849, 23250]  # List of customers
RW = ['HDC_R', 'HDC_A', 'UPS_R', 'UPS_A']  # List of warehouses

for j in RC:
    for i in RW:
        # This constraint ensures that no flow is assigned from customer j to warehouse k
        model.addConstr(
            sum(x[i, j, k] for k in materials) == 0,
            name=f"demand_{j}_{k}")


# SKUs not available for UPS
RK = [10252926, 10246447, 11021224, 11008092, 11008082, 11007471, 11005596, 10238766]  # List of SKUs
RUPS = ['UPS_R', 'UPS_A']  # List of warehouses

for j in RK:
    for i in RUPS:
        # This constraint ensures that no flow is assigned from customer j to warehouse k
        model.addConstr(
            sum(x[i, j, k] for j in customers) == 0,
            name=f"demand_{j}_{k}")



In [66]:
# Solve model
model.optimize()

Gurobi Optimizer version 12.0.2 build v12.0.2rc0 (linux64 - "Ubuntu 22.04.4 LTS")

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license 2575051 - for non-commercial use only - registered to di___@mit.edu
Optimize a model with 236942 rows, 1418310 columns and 2875384 nonzeros
Model fingerprint: 0x598b4a31
Variable types: 1417692 continuous, 618 integer (0 binary)
Coefficient statistics:
  Matrix range     [5e-05, 1e+00]
  Objective range  [2e-01, 9e+12]
  Bounds range     [0e+00, 0e+00]
  RHS range        [5e-01, 1e+05]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Presolve removed 250 rows and 6850 columns (presolve time = 5s)...
Presolve removed 216131 rows and 1298396 columns
Presolve time: 8.05s
Presolved: 20811 rows, 119914 columns, 128755 nonzeros
Variable types: 119506 continuous, 408 integer (73 binary)


## **Solution visualization and analysis**

In [67]:
# Table: Objective values

# Objective value
objective_value = model.ObjVal

# Total transportation cost
total_cost = sum(tc[i, j, k] * x[i, j, k].X for i in W for j in C for k in K)

# Total emissions
total_emissions = sum(em[i, j, k] * x[i, j, k].X for i in W for j in C for k in K)

# Create one-row DataFrame with 'Scenario' column first
objective_df = pd.DataFrame([{
    'Scenario': 'Optimal',
    'Objective Value': objective_value,
    'Total Transportation Cost': total_cost,
    'Total Emissions': total_emissions
}])

display(objective_df)

Scenario  Objective Value  Total Transportation Cost  Total Emissions
0  Optimal     5.035612e+07               4.690413e+07     1.545204e+08

In [68]:
# Table: detailed results

import pandas as pd

# Assuming model.status == GRB.OPTIMAL
if model.status == GRB.OPTIMAL:
    results = []  # List to collect the results for the first DataFrame

    # Collect results for the first DataFrame
    for i in W:
        for j in C:
            for k in K:
                if x[i, j, k].X > 0:
                    results.append({
                        'Warehouse': i,
                        'Customer': j,
                        'Material': k,
                        'Value': x[i, j, k].X
                    })

    # Create the first DataFrame (for the x values)
    x_df = pd.DataFrame(results)
x_df

Warehouse  Customer  Material  Value
0          KDC_R      1506  11020776    0.5
1          KDC_R      1509  11020776    0.5
2          KDC_R      1510  11020776    0.5
3          KDC_R      1783  11020776    0.5
4          KDC_R      1969  11020776    0.5
...          ...       ...       ...    ...
236277     UPS_A  90591500  10202719    0.5
236278     UPS_A  90591500  10215579    0.5
236279     UPS_A  90591500  10238766    0.5
236280     UPS_A  90591500  10206065    0.5
236281     UPS_A  90591500  10233000    0.5

[236282 rows x 4 columns]

In [69]:
# Table: COGS by warehouse

# Merge x_df with materials_df to add units_pallet and cost
x_df = x_df.merge(materials_df[['material_id', 'units_pallet', 'cost']],
                   left_on='Material',
                   right_on='material_id',
                   how='left')

# Drop redundant material_id column after merge
x_df.drop(columns=['material_id'], inplace=True)

x_df['cost'] = pd.to_numeric(x_df['cost'], errors='coerce')
x_df['pallets_used'] = x_df['Value'] / x_df['units_pallet']
x_df['total_cost'] = x_df['Value'] * x_df['cost']

x_df


# Build COGS summary
COGS = pd.DataFrame([{
    'Scenario': 'Optimal',
    'KDC': x_df[x_df['Warehouse'].str.startswith('KDC')]['total_cost'].sum(),
    'UPS': x_df[x_df['Warehouse'].str.startswith('UPS')]['total_cost'].sum(),
    'HDC': x_df[x_df['Warehouse'].str.startswith('HDC')]['total_cost'].sum()
}])

display(COGS)

Scenario           KDC           UPS           HDC
0  Optimal  2.281609e+10  4.526512e+09  3.466318e+09

In [70]:
#Summary
import pandas as pd

# Grouping by warehouse and counting unique customers
customers_per_warehouse = x_df.groupby('Warehouse')['Customer'].nunique()
customers_per_warehouse_grouped = x_df.groupby(x_df['Warehouse'].str[:3])['Customer'].nunique()

# Filter for values > 0.5
# This filter omits fake demand that was added for visibility
filtered_df = x_df[x_df['Value'] > 0.5]

# Grouping by warehouse and counting unique materials
materials_per_warehouse = filtered_df.groupby('Warehouse')['Material'].nunique()
materials_per_warehouse_grouped = filtered_df.groupby(filtered_df['Warehouse'].str[:3])['Material'].nunique()

# Total pallets used per warehouse
pallets_per_warehouse = x_df.groupby('Warehouse')['pallets_used'].sum()

# Total cost per warehouse
cost_per_warehouse = x_df.groupby('Warehouse')['total_cost'].sum()
cost_per_warehouse_grouped = x_df.groupby(x_df['Warehouse'].str[:3])['total_cost'].sum()

# Total cost calculation
total_cost = x_df['total_cost'].sum()

# Percentage of total cost per warehouse
cost_percentage_per_warehouse = (cost_per_warehouse / total_cost) * 100
cost_percentage_per_warehouse_grouped = (cost_per_warehouse_grouped / total_cost) * 100

# Formatting as currency and percentage
cost_per_warehouse = cost_per_warehouse.apply(lambda x: "${:,.0f}".format(x))
cost_per_warehouse_grouped = cost_per_warehouse_grouped.apply(lambda x: "${:,.0f}".format(x))
cost_percentage_per_warehouse = cost_percentage_per_warehouse.apply(lambda x: "{:.2f}%".format(x))
cost_percentage_per_warehouse_grouped = cost_percentage_per_warehouse_grouped.apply(lambda x: "{:.2f}%".format(x))

# Display results
print("Customers per warehouse:\n", customers_per_warehouse)
print("\nCustomers per grouped warehouse:\n", customers_per_warehouse_grouped)

print("\nMaterials per warehouse:\n", materials_per_warehouse)
print("\nMaterials per grouped warehouse:\n", materials_per_warehouse_grouped)

print("\nPallets used per warehouse:\n", pallets_per_warehouse)

print("\nTotal cost per warehouse:\n", cost_per_warehouse)
print("\nTotal cost per grouped warehouse:\n", cost_per_warehouse_grouped)

print("\nCost percentage per warehouse:\n", cost_percentage_per_warehouse)
print("\nCost percentage per grouped warehouse:\n", cost_percentage_per_warehouse_grouped)


Customers per warehouse:
 Warehouse
HDC_A     517
HDC_R     517
KDC_A    1323
KDC_R    1777
UPS_A     454
UPS_R     454
Name: Customer, dtype: int64

Customers per grouped warehouse:
 Warehouse
HDC     517
KDC    1777
UPS     454
Name: Customer, dtype: int64

Materials per warehouse:
 Warehouse
HDC_A    14
HDC_R    55
KDC_A    24
KDC_R    64
UPS_A    25
UPS_R    60
Name: Material, dtype: int64

Materials per grouped warehouse:
 Warehouse
HDC    69
KDC    88
UPS    85
Name: Material, dtype: int64

Pallets used per warehouse:
 Warehouse
HDC_A     16.078498
HDC_R     78.169459
KDC_A     75.812442
KDC_R    725.890470
UPS_A     47.568237
UPS_R    340.202027
Name: pallets_used, dtype: float64

Total cost per warehouse:
 Warehouse
HDC_A       $274,349,113
HDC_R     $3,191,968,708
KDC_A     $1,525,024,367
KDC_R    $21,291,063,615
UPS_A       $353,746,603
UPS_R     $4,172,765,566
Name: total_cost, dtype: object

Total cost per grouped warehouse:
 Warehouse
HDC     $3,466,317,821
KDC    $22,816,

In [71]:
# Results document for dashboard

# Extract decision variable values after optimization
x_solution = {(i, j, k): x[i, j, k].X for i in W for j in C for k in K if x[i, j, k].X > 0}

# Create a DataFrame from x_solution
df = pd.DataFrame([
    {'Warehouse': i, 'Customer': j, 'Material': k, 'Value': x_solution[i, j, k]}
    for (i, j, k) in x_solution
])

# Compute total cost per (warehouse, customer)
df['t_cost'] = df.apply(lambda row: tc[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)

# Compute emissions per (warehouse, customer)
df['emissions'] = df.apply(lambda row: em[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)

# Aggregate results for Table 1
table_1 = df.groupby(['Customer', 'Warehouse']).agg(
    t_cost=('t_cost', 'sum'),
    emissions=('emissions', 'sum')
).reset_index()


# Rename 'Customer' column to 'customer_id' for merging
table_1.rename(columns={'Customer': 'customer_id'}, inplace=True)  # This line is the key change

# Merge with customer names and zip codes (assuming a lookup DataFrame `customers_df`)
table_1 = table_1.merge(customers_df[['customer_id', 'customer_name', 'zipcode']], on='customer_id', how='left')

# Renaming columns
table_1.rename(columns={'Customer': 'customer_ID'}, inplace=True)

# Aggregate results for Table 2
table_2 = df.groupby(['Material', 'Warehouse', 'Customer']).agg(
    demand_served=('Value', 'sum')
).reset_index()

# Creating warehouse-material-customer ID
table_2['key'] = (
    table_2['Warehouse'] + "-" + table_2['Material'].astype(str) + "-" + table_2['Customer'].astype(str)
)

# Ensure 'cost' column is of string type before applying .str.replace
materials_df['cost'] = materials_df['cost'].astype(str).str.replace(',', '', regex=True).astype(float)

# Merge with material metadata (assuming a lookup DataFrame `df_materials`)
# CHANGED: Use 'Material' to merge with 'material_id' from df_materials and get the 'cost'
table_2 = table_2.merge(materials_df[['material_id', 'material_name', 'rev_class', 'med_class', 'cost',]],
                        left_on='Material', right_on='material_id', how='left')
table_2


# Calculate 'materials_cogs' by multiplying 'demand_served' by the material's cost from df_materials
table_2['cogs'] = table_2['demand_served'] * table_2['cost'].astype(float)

# Remove the 'cost' column from df_materials as we now have 'materials_cogs'
table_2.drop(columns=['cost', 'material_id'], inplace=True)

# Renaming columns
# CHANGED: Removed the renaming of 'Material' to 'material_id' as it's already done during merge
table_2.rename(columns={'Customer': 'customer_id'}, inplace=True)


order1 = ['customer_id', 'customer_name', 'zipcode', 'Warehouse', 't_cost', 'emissions']
table_1 = table_1[order1]


order2 = ['key', 'Warehouse', 'Material',  'customer_id', 'material_name', 'rev_class', 'med_class', 'demand_served', 'cogs']
table_2 = table_2[order2]


# Define the file name
output_file = "model_results.xlsx"

# Create an Excel writer object
with pd.ExcelWriter(output_file, engine='xlsxwriter') as writer:
    # Write Table 1 to the first sheet
    table_1.to_excel(writer, sheet_name="Customers_Served", index=False)

    # Write Table 2 to the second sheet
    table_2.to_excel(writer, sheet_name="Materials_Stored", index=False)

In [72]:
# Group and sum the 'Value' column
demand_summary = x_df.groupby(['Warehouse', 'Material'], as_index=False)['Value'].sum()

# Save to CSV in the same folder
output_file = os.path.join(folder_path, "m_demand_wh.csv")
demand_summary.to_csv(output_file, index=False)

## **Scenarios**

### **Scenario 0: Current State**

In [74]:
# Setup: create dictionaries
customer_hub = customers_df.set_index('customer_id')['h_served_from'].to_dict()
material_zone = materials_df.set_index('material_id')['t_zone'].to_dict()
warehouse_zone = warehouses_df.set_index('warehouse_id')['t_zone'].to_dict()
warehouse_prefix = {wid: wid[:3] for wid in W}

# Step 1: Assign demand based on h_served_from and t_zone
x_result = {}
for c in C:
    allowed_prefix = customer_hub[c]
    for w in W:
        if warehouse_prefix[w] != allowed_prefix:
            continue  # skip warehouses outside allowed hub
        for k in K:
            if material_zone[k] != warehouse_zone[w]:
                continue  # skip incompatible temp zone
            demand = gamma.get((c, k), 0)
            x_result[(w, c, k)] = demand
        # For disallowed temp zones, explicitly set to 0
        for k in K:
            if material_zone[k] != warehouse_zone[w]:
                x_result[(w, c, k)] = 0
    # For disallowed prefixes, explicitly set to 0
    for w in W:
        if warehouse_prefix[w] != allowed_prefix:
            for k in K:
                x_result[(w, c, k)] = 0


# Table: Objective values

# Step 2: Compute cost, emissions, objective
total_cost = sum(tc[i, j, k] * x_result[i, j, k] for (i, j, k) in x_result)
total_emissions = sum(em[i, j, k] * x_result[i, j, k] for (i, j, k) in x_result)
objective_value = w_c * total_cost + w_e * total_emissions

# Step 5: Add to summary tables
new_obj_row = pd.DataFrame([{
    'Scenario': 'Current State',
    'Objective Value': objective_value,
    'Total Transportation Cost': total_cost,
    'Total Emissions': total_emissions
}])
objective_df = pd.concat([objective_df, new_obj_row], ignore_index=True)



# Table: detailed results

x_df = pd.DataFrame([
    {'Warehouse': i, 'Customer': j, 'Material': k, 'Value': v}
    for (i, j, k), v in x_result.items() if v > 0
])

x_df = x_df.merge(materials_df[['material_id', 'units_pallet', 'cost']],
                  left_on='Material', right_on='material_id', how='left')
x_df.drop(columns=['material_id'], inplace=True)
x_df['cost'] = pd.to_numeric(x_df['cost'], errors='coerce')
x_df['pallets_used'] = x_df['Value'] / x_df['units_pallet']
x_df['total_cost'] = x_df['Value'] * x_df['cost']


new_cogs_row = pd.DataFrame([{
    'Scenario': 'Current State',
    'KDC': x_df[x_df['Warehouse'].str.startswith('KDC')]['total_cost'].sum(),
    'UPS': x_df[x_df['Warehouse'].str.startswith('UPS')]['total_cost'].sum(),
    'HDC': x_df[x_df['Warehouse'].str.startswith('HDC')]['total_cost'].sum()
}])
COGS = pd.concat([COGS, new_cogs_row], ignore_index=True)

In [75]:
display(objective_df)
display(COGS)

Scenario  Objective Value  Total Transportation Cost  Total Emissions
0        Optimal     5.035612e+07               4.690413e+07     1.545204e+08
1  Current State     1.430409e+08               5.282203e+07     1.731139e+08

Scenario           KDC           UPS           HDC
0        Optimal  2.281609e+10  4.526512e+09  3.466318e+09
1  Current State  2.136298e+10  4.057536e+09  5.388402e+09

In [76]:
# Create DataFrame from x_result
baseline_df = pd.DataFrame([
    {'Warehouse': i, 'Customer': j, 'Material': k, 'Value': val}
    for (i, j, k), val in x_result.items() if val > 0
])

# Compute total cost and emissions using tc and em
baseline_df['t_cost'] = baseline_df.apply(
    lambda row: tc[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)
baseline_df['emissions'] = baseline_df.apply(
    lambda row: em[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)

# Table 1: Total cost and emissions by customer and warehouse
table_1 = baseline_df.groupby(['Customer', 'Warehouse']).agg(
    t_cost=('t_cost', 'sum'),
    emissions=('emissions', 'sum')
).reset_index()

# Rename for merge
table_1.rename(columns={'Customer': 'customer_id'}, inplace=True)
table_1 = table_1.merge(customers_df[['customer_id', 'customer_name', 'zipcode']], on='customer_id', how='left')
table_1 = table_1[['customer_id', 'customer_name', 'zipcode', 'Warehouse', 't_cost', 'emissions']]

# Table 2: Demand served by material, customer, warehouse
table_2 = baseline_df.groupby(['Material', 'Warehouse', 'Customer']).agg(
    demand_served=('Value', 'sum')
).reset_index()

# Create unique key
table_2['key'] = (
    table_2['Warehouse'] + "-" + table_2['Material'].astype(str) + "-" + table_2['Customer'].astype(str)
)

# Ensure cost is numeric
materials_df['cost'] = materials_df['cost'].astype(str).str.replace(',', '', regex=True).astype(float)

# Merge with material metadata
table_2 = table_2.merge(
    materials_df[['material_id', 'material_name', 'rev_class', 'med_class', 'cost']],
    left_on='Material',
    right_on='material_id',
    how='left'
)

# Calculate COGS
table_2['cogs'] = table_2['demand_served'] * table_2['cost']

# Clean up
table_2.drop(columns=['cost', 'material_id'], inplace=True)
table_2.rename(columns={'Customer': 'customer_id'}, inplace=True)

# Reorder columns
table_2 = table_2[['key', 'Warehouse', 'Material', 'customer_id',
                   'material_name', 'rev_class', 'med_class', 'demand_served', 'cogs']]

# Save to Excel
with pd.ExcelWriter("model_0_results.xlsx", engine='xlsxwriter') as writer:
    table_1.to_excel(writer, sheet_name="Customers_Served", index=False)
    table_2.to_excel(writer, sheet_name="Materials_Stored", index=False)

### **Scenario 1: No Customer-WH Constraint**

In [77]:
# Decision variables
x = model.addVars(W, C, K, vtype=GRB.CONTINUOUS, name="flow")
pallets_used = model.addVars(W, K, vtype=GRB.INTEGER, name="pallets_used")

t_cost = sum(
    tc[i, j, k] * x[i, j, k]
    for i in W for j in C for k in K
)

emissions = sum(
    em[i, j, k] * x[i, j, k]
    for i in W for j in C for k in K
)

# Set the objective to minimize the weighted sum of cost and emissions
model.setObjective(w_c * t_cost + w_e * emissions, GRB.MINIMIZE)




# Constraints

# Demand satisfaction constraint
for j in C:
    for k in K:
        model.addConstr(
            sum(x[i, j, k] for i in W) >= gamma[j, k],
            name=f"demand_{j}_{k}")

# Warehouse capacity constraint
for i in W:
        for k in K:
            model.addConstr(
                pallets_used[i, k] >= gp.quicksum(x[i, j, k] / u[k] for j in C),
                name=f"pallet_calc_{i}_{k}"
            )

        # Ensure total pallets used do not exceed warehouse capacity
        model.addConstr(
            gp.quicksum(pallets_used[i, k] for k in K) <= s[i],
            name=f"capacity_{i}"
        )

# SKUs not available for UPS
RK = [10252926, 10246447, 11021224, 11008092, 11008082, 11007471, 11005596, 10238766]  # List of SKUs
RUPS = ['UPS_R', 'UPS_A']  # List of warehouses

for j in RK:
    for i in RUPS:
        # This constraint ensures that no flow is assigned from customer j to warehouse k
        model.addConstr(
            sum(x[i, j, k] for j in customers) == 0,
            name=f"demand_{j}_{k}")

# Solve model
model.optimize()

Gurobi Optimizer version 12.0.2 build v12.0.2rc0 (linux64 - "Ubuntu 22.04.4 LTS")

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Academic license 2575051 - for non-commercial use only - registered to di___@mit.edu
Optimize a model with 473864 rows, 2836620 columns and 5748708 nonzeros
Model fingerprint: 0xf3162676
Variable types: 2835384 continuous, 1236 integer (0 binary)
Coefficient statistics:
  Matrix range     [5e-05, 1e+00]
  Objective range  [2e-01, 9e+12]
  Bounds range     [0e+00, 0e+00]
  RHS range        [5e-01, 1e+05]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.

Processing MIP start from previous solve: 0 nodes explored in subMIP, total elapsed time 5s
MIP start from previous solve produced solution with objective 5.02818e+07 (9.21s)
Loaded MIP start from previous solve with objective 5.02818e+07
Processed 

In [78]:
# Table: Objective values

# Objective value
objective_value = model.ObjVal

# Total transportation cost
total_cost = sum(tc[i, j, k] * x[i, j, k].X for i in W for j in C for k in K)

# Total emissions
total_emissions = sum(em[i, j, k] * x[i, j, k].X for i in W for j in C for k in K)

# Create one-row DataFrame with 'Scenario' column first
new_row = pd.DataFrame([{
    'Scenario': 'No Customers Constraint',
    'Objective Value': objective_value,
    'Total Transportation Cost': total_cost,
    'Total Emissions': total_emissions
}])

objective_df = pd.concat([objective_df, new_row], ignore_index=True)
display(objective_df)

Scenario  Objective Value  Total Transportation Cost  \
0                  Optimal     5.035612e+07               4.690413e+07   
1            Current State     1.430409e+08               5.282203e+07   
2  No Customers Constraint     5.028182e+07               4.682535e+07   

   Total Emissions  
0     1.545204e+08  
1     1.731139e+08  
2     1.543020e+08

In [79]:
# Results document for dashboard

# Extract decision variable values after optimization
x_solution = {(i, j, k): x[i, j, k].X for i in W for j in C for k in K if x[i, j, k].X > 0}

# Create a DataFrame from x_solution
df = pd.DataFrame([
    {'Warehouse': i, 'Customer': j, 'Material': k, 'Value': x_solution[i, j, k]}
    for (i, j, k) in x_solution
])

# Compute total cost per (warehouse, customer)
df['t_cost'] = df.apply(lambda row: tc[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)

# Compute emissions per (warehouse, customer)
df['emissions'] = df.apply(lambda row: em[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)

# Aggregate results for Table 1
table_1 = df.groupby(['Customer', 'Warehouse']).agg(
    t_cost=('t_cost', 'sum'),
    emissions=('emissions', 'sum')
).reset_index()


# Rename 'Customer' column to 'customer_id' for merging
table_1.rename(columns={'Customer': 'customer_id'}, inplace=True)  # This line is the key change

# Merge with customer names and zip codes (assuming a lookup DataFrame `customers_df`)
table_1 = table_1.merge(customers_df[['customer_id', 'customer_name', 'zipcode']], on='customer_id', how='left')

# Renaming columns
table_1.rename(columns={'Customer': 'customer_ID'}, inplace=True)

# Aggregate results for Table 2
table_2 = df.groupby(['Material', 'Warehouse', 'Customer']).agg(
    demand_served=('Value', 'sum')
).reset_index()

# Creating warehouse-material-customer ID
table_2['key'] = (
    table_2['Warehouse'] + "-" + table_2['Material'].astype(str) + "-" + table_2['Customer'].astype(str)
)

# Ensure 'cost' column is of string type before applying .str.replace
materials_df['cost'] = materials_df['cost'].astype(str).str.replace(',', '', regex=True).astype(float)

# Merge with material metadata (assuming a lookup DataFrame `df_materials`)
# CHANGED: Use 'Material' to merge with 'material_id' from df_materials and get the 'cost'
table_2 = table_2.merge(materials_df[['material_id', 'material_name', 'rev_class', 'med_class', 'cost',]],
                        left_on='Material', right_on='material_id', how='left')
table_2


# Calculate 'materials_cogs' by multiplying 'demand_served' by the material's cost from df_materials
table_2['cogs'] = table_2['demand_served'] * table_2['cost'].astype(float)

# Remove the 'cost' column from df_materials as we now have 'materials_cogs'
table_2.drop(columns=['cost', 'material_id'], inplace=True)

# Renaming columns
# CHANGED: Removed the renaming of 'Material' to 'material_id' as it's already done during merge
table_2.rename(columns={'Customer': 'customer_id'}, inplace=True)


order1 = ['customer_id', 'customer_name', 'zipcode', 'Warehouse', 't_cost', 'emissions']
table_1 = table_1[order1]


order2 = ['key', 'Warehouse', 'Material',  'customer_id', 'material_name', 'rev_class', 'med_class', 'demand_served', 'cogs']
table_2 = table_2[order2]


# Define the file name
output_file = "model_BigCust_results.xlsx"

# Create an Excel writer object
with pd.ExcelWriter(output_file, engine='xlsxwriter') as writer:
    # Write Table 1 to the first sheet
    table_1.to_excel(writer, sheet_name="Customers_Served", index=False)

    # Write Table 2 to the second sheet
    table_2.to_excel(writer, sheet_name="Materials_Stored", index=False)

In [80]:
# Table: detailed results

# Assuming model.status == GRB.OPTIMAL
if model.status == GRB.OPTIMAL:
    results = []  # List to collect the results for the first DataFrame

    # Collect results for the first DataFrame
    for i in W:
        for j in C:
            for k in K:
                if x[i, j, k].X > 0:
                    results.append({
                        'Warehouse': i,
                        'Customer': j,
                        'Material': k,
                        'Value': x[i, j, k].X
                    })

    # Create the first DataFrame (for the x values)
    x_df = pd.DataFrame(results)
x_df

# Merge x_df with materials_df to add units_pallet and cost
x_df = x_df.merge(materials_df[['material_id', 'units_pallet', 'cost']],
                   left_on='Material',
                   right_on='material_id',
                   how='left')

# Drop redundant material_id column after merge
x_df.drop(columns=['material_id'], inplace=True)

x_df['cost'] = pd.to_numeric(x_df['cost'], errors='coerce')
x_df['pallets_used'] = x_df['Value'] / x_df['units_pallet']
x_df['total_cost'] = x_df['Value'] * x_df['cost']

x_df


# Build COGS summary
new_row = pd.DataFrame([{
    'Scenario': 'No Customers Constraint',
    'KDC': x_df[x_df['Warehouse'].str.startswith('KDC')]['total_cost'].sum(),
    'UPS': x_df[x_df['Warehouse'].str.startswith('UPS')]['total_cost'].sum(),
    'HDC': x_df[x_df['Warehouse'].str.startswith('HDC')]['total_cost'].sum()
}])
COGS = pd.concat([COGS, new_row], ignore_index=True)
display(COGS)

Scenario           KDC           UPS           HDC
0                  Optimal  2.281609e+10  4.526512e+09  3.466318e+09
1            Current State  2.136298e+10  4.057536e+09  5.388402e+09
2  No Customers Constraint  1.541739e+10  1.192521e+10  3.466318e+09

In [ ]:
display(objective_df)
display(COGS)

### **Scenario 2: Value at Risk**

In [ ]:
max_cogs = 18

for max_cogs in range(18, 16, -2):
  limit = max_cogs * 1000000000
  # Decision variables
  x = model.addVars(W, C, K, vtype=GRB.CONTINUOUS, name="flow")
  pallets_used = model.addVars(W, K, vtype=GRB.INTEGER, name="pallets_used")

  t_cost = sum(
      tc[i, j, k] * x[i, j, k]
      for i in W for j in C for k in K
  )

  emissions = sum(
      em[i, j, k] * x[i, j, k]
      for i in W for j in C for k in K
  )

  # Set the objective to minimize the weighted sum of cost and emissions
  model.setObjective(w_c * t_cost + w_e * emissions, GRB.MINIMIZE)




  # Constraints

  # Demand satisfaction constraint
  for j in C:
      for k in K:
          model.addConstr(
              sum(x[i, j, k] for i in W) >= gamma[j, k],
              name=f"demand_{j}_{k}")

  # # Warehouse capacity constraint
  # for i in W:
  #         for k in K:
  #             model.addConstr(
  #                 pallets_used[i, k] >= gp.quicksum(x[i, j, k] / u[k] for j in C),
  #                 name=f"pallet_calc_{i}_{k}"
  #             )

  #         # Ensure total pallets used do not exceed warehouse capacity
  #         model.addConstr(
  #             gp.quicksum(pallets_used[i, k] for k in K) <= s[i],
  #             name=f"capacity_{i}"
  #         )

  # Big Customers only from KDC constraint
  RC = [90631576, 90584135, 90589939, 16849, 23250]  # List of customers
  RW = ['HDC_R', 'HDC_A', 'UPS_R', 'UPS_A']  # List of warehouses

  for j in RC:
      for i in RW:
          # This constraint ensures that no flow is assigned from customer j to warehouse k
          model.addConstr(
              sum(x[i, j, k] for k in materials) == 0,
              name=f"demand_{j}_{k}")


  # SKUs not available for UPS
  RK = [10252926, 10246447, 11021224, 11008092, 11008082, 11007471, 11005596, 10238766]  # List of SKUs
  RUPS = ['UPS_R', 'UPS_A']  # List of warehouses

  for j in RK:
      for i in RUPS:
          # This constraint ensures that no flow is assigned from customer j to warehouse k
          model.addConstr(
              sum(x[i, j, k] for j in customers) == 0,
              name=f"demand_{j}_{k}")

  kdc_warehouses = ['KDC_R', 'KDC_A']
  model.addConstr(
      gp.quicksum(x[i, j, k] * materials[k].cost for i in kdc_warehouses for j in C for k in K) <= limit,
      name="cogs_limit_KDC"
  )

  hdc_warehouses = ['HDC_R', 'HDC_A']
  model.addConstr(
      gp.quicksum(x[i, j, k] * materials[k].cost for i in hdc_warehouses for j in C for k in K) <= limit,
      name="cogs_limit_HDC"
  )

  ups_warehouses = ['UPS_R', 'UPS_A']
  model.addConstr(
      gp.quicksum(x[i, j, k] * materials[k].cost for i in ups_warehouses for j in C for k in K) <= limit,
      name="cogs_limit_UPS"
  )

  # Solve model
  model.optimize()





  # Table: Objective values

  # Objective value
  objective_value = model.ObjVal

  # Total transportation cost
  total_cost = sum(tc[i, j, k] * x[i, j, k].X for i in W for j in C for k in K)

  # Total emissions
  total_emissions = sum(em[i, j, k] * x[i, j, k].X for i in W for j in C for k in K)

  # Create one-row DataFrame with 'Scenario' column first
  new_row = pd.DataFrame([{
      'Scenario': f'Max Value at Risk = ${max_cogs}B',
      'Objective Value': objective_value,
      'Total Transportation Cost': total_cost,
      'Total Emissions': total_emissions
  }])

  objective_df = pd.concat([objective_df, new_row], ignore_index=True)





  # Table: detailed results

  # Assuming model.status == GRB.OPTIMAL
  if model.status == GRB.OPTIMAL:
      results = []  # List to collect the results for the first DataFrame

      # Collect results for the first DataFrame
      for i in W:
          for j in C:
              for k in K:
                  if x[i, j, k].X > 0:
                      results.append({
                          'Warehouse': i,
                          'Customer': j,
                          'Material': k,
                          'Value': x[i, j, k].X
                      })

      # Create the first DataFrame (for the x values)
      x_df = pd.DataFrame(results)
  x_df

  # Merge x_df with materials_df to add units_pallet and cost
  x_df = x_df.merge(materials_df[['material_id', 'units_pallet', 'cost']],
                     left_on='Material',
                     right_on='material_id',
                     how='left')

  # Drop redundant material_id column after merge
  x_df.drop(columns=['material_id'], inplace=True)

  x_df['cost'] = pd.to_numeric(x_df['cost'], errors='coerce')
  x_df['pallets_used'] = x_df['Value'] / x_df['units_pallet']
  x_df['total_cost'] = x_df['Value'] * x_df['cost']

  x_df


  # Build COGS summary
  new_row = pd.DataFrame([{
      'Scenario': f'Max Value at Risk = ${max_cogs}B',
      'KDC': x_df[x_df['Warehouse'].str.startswith('KDC')]['total_cost'].sum(),
      'UPS': x_df[x_df['Warehouse'].str.startswith('UPS')]['total_cost'].sum(),
      'HDC': x_df[x_df['Warehouse'].str.startswith('HDC')]['total_cost'].sum()
  }])
  COGS = pd.concat([COGS, new_row], ignore_index=True)

In [ ]:
display(objective_df)
display(COGS)

In [ ]:
# Results document for dashboard

# Extract decision variable values after optimization
x_solution = {(i, j, k): x[i, j, k].X for i in W for j in C for k in K if x[i, j, k].X > 0}

# Create a DataFrame from x_solution
df = pd.DataFrame([
    {'Warehouse': i, 'Customer': j, 'Material': k, 'Value': x_solution[i, j, k]}
    for (i, j, k) in x_solution
])

# Compute total cost per (warehouse, customer)
df['t_cost'] = df.apply(lambda row: tc[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)

# Compute emissions per (warehouse, customer)
df['emissions'] = df.apply(lambda row: em[row['Warehouse'], row['Customer'], row['Material']] * row['Value'], axis=1)

# Aggregate results for Table 1
table_1 = df.groupby(['Customer', 'Warehouse']).agg(
    t_cost=('t_cost', 'sum'),
    emissions=('emissions', 'sum')
).reset_index()


# Rename 'Customer' column to 'customer_id' for merging
table_1.rename(columns={'Customer': 'customer_id'}, inplace=True)  # This line is the key change

# Merge with customer names and zip codes (assuming a lookup DataFrame `customers_df`)
table_1 = table_1.merge(customers_df[['customer_id', 'customer_name', 'zipcode']], on='customer_id', how='left')

# Renaming columns
table_1.rename(columns={'Customer': 'customer_ID'}, inplace=True)

# Aggregate results for Table 2
table_2 = df.groupby(['Material', 'Warehouse', 'Customer']).agg(
    demand_served=('Value', 'sum')
).reset_index()

# Creating warehouse-material-customer ID
table_2['key'] = (
    table_2['Warehouse'] + "-" + table_2['Material'].astype(str) + "-" + table_2['Customer'].astype(str)
)

# Ensure 'cost' column is of string type before applying .str.replace
materials_df['cost'] = materials_df['cost'].astype(str).str.replace(',', '', regex=True).astype(float)

# Merge with material metadata (assuming a lookup DataFrame `df_materials`)
# CHANGED: Use 'Material' to merge with 'material_id' from df_materials and get the 'cost'
table_2 = table_2.merge(materials_df[['material_id', 'material_name', 'rev_class', 'med_class', 'cost',]],
                        left_on='Material', right_on='material_id', how='left')
table_2


# Calculate 'materials_cogs' by multiplying 'demand_served' by the material's cost from df_materials
table_2['cogs'] = table_2['demand_served'] * table_2['cost'].astype(float)

# Remove the 'cost' column from df_materials as we now have 'materials_cogs'
table_2.drop(columns=['cost', 'material_id'], inplace=True)

# Renaming columns
# CHANGED: Removed the renaming of 'Material' to 'material_id' as it's already done during merge
table_2.rename(columns={'Customer': 'customer_id'}, inplace=True)


order1 = ['customer_id', 'customer_name', 'zipcode', 'Warehouse', 't_cost', 'emissions']
table_1 = table_1[order1]


order2 = ['key', 'Warehouse', 'Material',  'customer_id', 'material_name', 'rev_class', 'med_class', 'demand_served', 'cogs']
table_2 = table_2[order2]


# Define the file name
output_file = "model_VaR18_results.xlsx"

# Create an Excel writer object
with pd.ExcelWriter(output_file, engine='xlsxwriter') as writer:
    # Write Table 1 to the first sheet
    table_1.to_excel(writer, sheet_name="Customers_Served", index=False)

    # Write Table 2 to the second sheet
    table_2.to_excel(writer, sheet_name="Materials_Stored", index=False)